<a href="https://colab.research.google.com/github/sudhanshu2/propagate-alerts/blob/master/simulations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Alert Propagation on EdgeSys
This notebook contains the simulations for the Alert Propagation API implemented on EdgeSys. Please refer to the `README` in the Github repository for further information.

# Graph Creation
This section contains specifications for the graph, including the number of total sensors and the number of sensors each sensor is connected to in the decentralized system. 

In [ ]:
%matplotlib inline
import networkx as nx
import matplotlib.pyplot as plt

def create_current(number_sensors):
  G_curr = nx.Graph()
  for i in range(number_sensors):
    G_curr.add_node(i, visited="false")
    
  for i in range(1, number_sensors):
    G_curr.add_edge(0, i)
  return G_curr

In [ ]:
%matplotlib inline
import networkx as nx
import matplotlib.pyplot as plt
from math import log
import secrets

def create_alert_graph(number_sensors, connected_sensors, random_connections=False):
  random_generator = secrets.SystemRandom()
  max_connected_sensors = connected_sensors

  G_alert = nx.Graph()
  for i in range(number_sensors):
    G_alert.add_node(i, visited="false")
  
  if random_connections is True:
    connected_sensors = random_generator.randrange(1, max_connected_sensors)
  for i in range(1, connected_sensors + 1):
    G_alert.add_edge(0, i)
    
  current_node = 1
  current_difference = connected_sensors
  
  while current_node + current_difference <= number_sensors:
    if random_connections is True:
      connected_sensors = random_generator.randrange(1, max_connected_sensors)
    for i in range(connected_sensors - 1):
      to_join = current_node + current_difference + i
      if current_node < number_sensors and to_join < number_sensors:
        G_alert.add_edge(current_node, to_join)
    current_node += 1
    current_difference += connected_sensors - 2
  return G_alert

# Graph Visualization
This section contains visualizations for the graphs.

In [ ]:
import networkx as nx

from bokeh.io import show, output_notebook
from bokeh.plotting import figure, from_networkx

output_notebook()

G = create_current(1000)


plot = figure(title="Centralized Node Network", x_range=(-2.2,2.2), y_range=(-2.2,2.2),
              tools="", toolbar_location=None)

graph = from_networkx(G, nx.spring_layout, scale=2, center=(0,0))
plot.axis.visible = False
plot.renderers.append(graph)

show(plot)

In [ ]:
import networkx as nx

from bokeh.io import show, output_notebook
from bokeh.plotting import figure, from_networkx

output_notebook()

G = create_alert_graph(1000, 5)

plot = figure(title="Edge Based Node Network", x_range=(-2.2,2.2), y_range=(-2.2,2.2),
              tools="", toolbar_location=None)

graph = from_networkx(G, nx.spring_layout, scale=2, center=(0,0))
plot.axis.visible = False
plot.renderers.append(graph)

show(plot)

# Simulation
This section contains the code for simulating the network structure under different conditions. The ```G``` specied in the first code block is the graph used for simulations.  



In [ ]:
from collections import defaultdict

def alert_time_simulation(G, alert_origin, multiplier=1.0):
  for node in G.nodes:
    G.nodes[node]["visited"] = "false"

  normalized_latency_multiplier = (200.0 / len(G.nodes())) * multiplier
    
  not_visited_neighbors = list()
  G_visited = defaultdict(list)
    
  not_visited_neighbors.append(alert_origin)
  G.nodes[alert_origin]["visited"] = "true"
  G_visited[0].append(alert_origin)  
  time_stamps = set()
    
  while len(not_visited_neighbors) != 0:
    current = not_visited_neighbors.pop()
    for edge in G.edges(current):
      if G.nodes[edge[1]]["visited"] == "false":
        not_visited_neighbors.append(edge[1])
        G.nodes[edge[1]]["visited"] = "true"
        latency = int(normalized_latency_multiplier * abs(edge[1] - edge[0]))
        G_visited[latency].append(edge[1])      
        time_stamps.add(latency)
          
  sorted_time_stamps = list(time_stamps)
  sorted_time_stamps.sort()
  
  time_stamp = list()
  nodes_alerted = list()
  current_nodes_alerted = 0
  
  for i in range(sorted_time_stamps[len(sorted_time_stamps) - 1] + 1):
    if i in G_visited:
      current_nodes_alerted += len(G_visited[i])
    time_stamp.append(i)
    nodes_alerted.append(current_nodes_alerted)
  return time_stamp, nodes_alerted

In [ ]:
import secrets
import decimal

ctx = decimal.Context()
ctx.prec = 20

def float_to_str(f):
    d1 = ctx.create_decimal(repr(f))
    return format(d1, 'f')

def event_failure(probability):
  if probability >= 1:
    return True
  probability_string = float_to_str(probability) 
  decimals = probability_string[probability_string.index(".") + 1:]
  chance = int(decimals)
  precision = len(decimals)
  upper_range = pow(10, precision)

  random_generator = secrets.SystemRandom()
  generated = random_generator.randrange(1, upper_range)

  if generated <= chance:
    return True
  return False

In [81]:
from collections import defaultdict

FIBER_MULTIPLIER = 0.75

def alert_time_simulation_failure(G, alert_origin, multiplier=1.0, failure=False, failure_rate=0.2):
  for node in G.nodes:
    G.nodes[node]["visited"] = "false"

  normalized_latency_multiplier = (200.0 / len(G.nodes())) * multiplier
    
  not_visited_neighbors = list()
  G_visited = defaultdict(list)
    
  not_visited_neighbors.append(alert_origin)
  G.nodes[alert_origin]["visited"] = "true"
  G_visited[0].append(alert_origin)  
  time_stamps = set()
    
  while len(not_visited_neighbors) != 0:
    current = not_visited_neighbors.pop()
    neighbors = G.edges(current)
    to_remove = list()
    if failure == True:
      for edge in neighbors:
        probability = failure_rate * (1 - (abs(edge[1] - edge[0])) / (float) (len(G.nodes)))
        if event_failure(probability) == True:
          to_remove.append(edge)
    
    for edge in to_remove:
      G.remove_edge(edge[1], edge[0])

    for edge in G.edges(current):
      if G.nodes[edge[1]]["visited"] == "false":
        not_visited_neighbors.append(edge[1])
        G.nodes[edge[1]]["visited"] = "true"
        latency = int(normalized_latency_multiplier * abs(edge[1] - edge[0]))
        G_visited[latency].append(edge[1])      
        time_stamps.add(latency)
          
  sorted_time_stamps = list(time_stamps)
  sorted_time_stamps.sort()
  
  time_stamp = list()
  nodes_alerted = list()
  current_nodes_alerted = 0

  if len(sorted_time_stamps) == 0:
    return list(), list(), 0

  for i in range(sorted_time_stamps[len(sorted_time_stamps) - 1] + 1):
    if i in G_visited:
      current_nodes_alerted += len(G_visited[i])
    time_stamp.append(i)
    nodes_alerted.append(current_nodes_alerted)
  return time_stamp, nodes_alerted, current_nodes_alerted

### Simulation Decentralized Alert 
This is a set of simulations exclusive to the decentralized alert system.

#### Failure of Nodes
The failure rate of node reduces away from the node where the alert originates

In [84]:
import secrets
import sys

from bokeh.plotting import figure, show, output_notebook
from bokeh.layouts import row
from bokeh.models import WheelZoomTool, ResetTool, BoxZoomTool, SaveTool

NUMBER_NODES = 1000
MIN_FAILURE = 0.00001
MAX_FAILURE = 1
STEP = 0.00001
NUMBER_RUNS = 20
NODE_CONNECTIONS = 20

current_failure_rate = MIN_FAILURE

alert_origin = list()
G_alert = list()
G_alert_random = list()
G_curr = create_current(NUMBER_NODES)

random_generator = secrets.SystemRandom()

for i in range(NUMBER_RUNS):  
  G_alert.append(create_alert_graph(NUMBER_NODES, NODE_CONNECTIONS))
  G_alert_random.append(create_alert_graph(NUMBER_NODES, NODE_CONNECTIONS, True))
  alert_origin.append(random_generator.randrange(1, NUMBER_NODES))

total_iterations = 1
all_zero = False

xs = [list()] * NUMBER_RUNS
ys = [None] * NUMBER_RUNS
ys_random = [None] * NUMBER_RUNS
ys_random = [None] * NUMBER_RUNS
ys_curr = [None] * NUMBER_RUNS

for i in range(NUMBER_RUNS):
  ys[i] = list()
  ys_random[i] = list()
  ys_curr[i] = list()

while current_failure_rate <= MAX_FAILURE and all_zero == False:
  sys.stdout.write("\rcurrent failure rate: " + str(current_failure_rate) + ", total iterations: " + str(total_iterations))
  sys.stdout.flush()
  count = 0

  for i in range(NUMBER_RUNS):    
    _, _, total_nodes_alerted = alert_time_simulation_failure(G_alert[i], alert_origin[i], failure=True, failure_rate=current_failure_rate)
    _, _, total_nodes_alerted_random = alert_time_simulation_failure(G_alert_random[i], alert_origin[i], failure=True, failure_rate=current_failure_rate)
    _, _, total_nodes_alerted_curr = alert_time_simulation_failure(G_curr, alert_origin[i], multiplier=FIBER_MULTIPLIER, failure=True, failure_rate=current_failure_rate)

    ys[i].append(total_nodes_alerted)
    ys_random[i].append(total_nodes_alerted_random)
    ys_curr[i].append(total_nodes_alerted_curr)

    if total_nodes_alerted == 0 and total_nodes_alerted_random == 0 and total_nodes_alerted_curr == 0:
      count += 1
    
    total_iterations += 1

  if count == NUMBER_RUNS:
    all_zero = True
  
  xs[0].append(current_failure_rate)
  current_failure_rate += STEP

sys.stdout.write("\r")
sys.stdout.flush()

if all_zero == True:
    print("current failure rate: " + str(current_failure_rate))

output_notebook()

p_fixed = figure(title="Fixed number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
r_fixed = p_fixed.multi_line(xs, ys, color="#000000", line_alpha=0.6, line_width=0.5)
p_fixed.add_layout(r_fixed)
p_fixed.xaxis.axis_label = "total time"
p_fixed.yaxis.axis_label = "total nodes"
p_fixed.toolbar.logo = None

p_random = figure(title="Random number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
r_random = p_random.multi_line(xs, ys_random, color="#000000", line_alpha=0.6, line_width=0.5)
p_random.add_layout(r_random)
p_random.xaxis.axis_label = "total time"
p_random.yaxis.axis_label = "total nodes"
p_random.toolbar.logo = None

p_curr = figure(title="Centralized Network", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
r_curr = p_curr.multi_line(xs, ys_curr, color="#000000", line_alpha=0.6, line_width=0.5)
p_curr.add_layout(r_curr)
p_curr.xaxis.axis_label = "total time"
p_curr.yaxis.axis_label = "total nodes"
p_curr.toolbar.logo = None

p = row(p_fixed, p_random, p_curr)
show(p)

current failure rate: 0.033139999999999475


#### Different Number of Nodes

In [82]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.layouts import row
import secrets

MIN_NODES = 100
MAX_NODES = 1000
NODE_CONNECTIONS = 10
STEP = 10

current_node_count = MIN_NODES

xs = list()
xs_random = list()
xs_curr = list()
ys = list()

while current_node_count <= MAX_NODES:
  G_alert = create_alert_graph(current_node_count, NODE_CONNECTIONS)
  G_alert_random = create_alert_graph(current_node_count, NODE_CONNECTIONS, True)
  G_curr = create_current(current_node_count)

  random_generator = secrets.SystemRandom()
  alert_origin = random_generator.randrange(1, current_node_count - 1)

  time_stamp, _ = alert_time_simulation(G_alert, alert_origin)
  time_stamp_random, _ = alert_time_simulation(G_alert_random, alert_origin)
  time_stamp_curr, _ = alert_time_simulation(G_curr, alert_origin, multiplier=FIBER_MULTIPLIER)

  xs.append(len(time_stamp))
  xs_random.append(len(time_stamp_random))
  xs_curr.append(len(time_stamp_curr))
  ys.append(current_node_count)

  current_node_count += STEP

output_notebook()

p_fixed = figure(title="Fixed number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_fixed.circle(xs, ys, size=5, color="#000000", alpha=0.5)
p_fixed.xaxis.axis_label = "total time"
p_fixed.yaxis.axis_label = "total nodes"
p_fixed.toolbar.logo = None

p_random = figure(title="Random number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_random.circle(xs_random, ys, size=5, color="#000000", alpha=0.5)
p_random.xaxis.axis_label = "total time"
p_random.yaxis.axis_label = "total nodes"
p_random.toolbar.logo = None

p_curr = figure(title="Centralized network", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_curr.circle(xs_curr, ys, size=5, color="#000000", alpha=0.5)
p_curr.xaxis.axis_label = "total time"
p_curr.yaxis.axis_label = "total nodes"
p_curr.toolbar.logo = None

p = row(p_fixed, p_random, p_curr)
show(p)

In [85]:
import secrets

from bokeh.plotting import figure, show, output_notebook
from bokeh.models import WheelZoomTool, ResetTool, BoxZoomTool, SaveTool

MIN_NODES = 100
MAX_NODES = 1000
NODE_CONNECTIONS = 10
STEP = 10

current_node_count = MIN_NODES

xs = list()
ys = list()
xs_random = list()
ys_random = list()
xs_curr = list()
ys_curr = list()

while current_node_count <= MAX_NODES:
  G_alert = create_alert_graph(current_node_count, NODE_CONNECTIONS)
  G_alert_random = create_alert_graph(current_node_count, NODE_CONNECTIONS, True)
  G_curr = create_current(current_node_count)

  random_generator = secrets.SystemRandom()
  alert_origin = random_generator.randrange(1, current_node_count - 1)

  time_stamp, nodes_alerted = alert_time_simulation(G_alert, alert_origin)
  time_stamp_random, nodes_alerted_random = alert_time_simulation(G_alert_random, alert_origin)
  time_stamp_curr, nodes_alerted_curr = alert_time_simulation(G_curr, alert_origin, multiplier=FIBER_MULTIPLIER)

  xs.append(time_stamp)
  ys.append(nodes_alerted)

  xs_random.append(time_stamp_random)
  ys_random.append(nodes_alerted_random)

  xs_curr.append(time_stamp_curr)
  ys_curr.append(nodes_alerted_curr)

  current_node_count += STEP

output_notebook()

p_fixed = figure(title="Fixed number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_fixed.xaxis.axis_label = "time"
p_fixed.yaxis.axis_label = "nodes"
for i in range(len(xs)):
  p_fixed.line(xs[i], ys[i], color="#000000", line_alpha=0.6, line_width=0.5)
p_fixed.toolbar.logo = None

p_random = figure(title="Random number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_random.xaxis.axis_label = "time"
p_random.yaxis.axis_label = "nodes"
for i in range(len(xs)):
  p_random.line(xs_random[i], ys_random[i], color="#000000", line_alpha=0.6, line_width=0.5)
p_random.toolbar.logo = None

p_curr = figure(title="Centralized network", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_curr.xaxis.axis_label = "time"
p_curr.yaxis.axis_label = "nodes"
for i in range(len(xs)):
  p_curr.line(xs_curr[i], ys_curr[i], color="#000000", line_alpha=0.6, line_width=0.5)
p_curr.toolbar.logo = None

p = row(p_fixed, p_random, p_curr)
show(p)

#### Different Origins

In [87]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.layouts import row
import secrets

NODES = 1000
NODE_CONNECTIONS = 10
NUMBER_LOOPS = 100

count = 0

xs = list()
ys = list()
xs_random = list()
xs_curr = list()

while count <= NUMBER_LOOPS:
  G_alert = create_alert_graph(NODES, NODE_CONNECTIONS)
  G_alert_random = create_alert_graph(NODES, NODE_CONNECTIONS, True)
  G_curr = create_current(NODES)

  random_generator = secrets.SystemRandom()
  alert_origin = random_generator.randrange(1, NODES - 1)

  time_stamp, _ = alert_time_simulation(G_alert, alert_origin)
  time_stamp_random, _ = alert_time_simulation(G_alert_random, alert_origin)
  time_stamp_curr, _ = alert_time_simulation(G_curr, alert_origin, multiplier=FIBER_MULTIPLIER)

  xs.append(len(time_stamp))
  xs_random.append(len(time_stamp_random))
  xs_curr.append(len(time_stamp_curr))
  ys.append(alert_origin)

  count += 1

output_notebook()

p_fixed = figure(title="Fixed number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_fixed.circle(xs, ys, size=5, color="#000000", alpha=0.5)
p_fixed.xaxis.axis_label = "total time"
p_fixed.yaxis.axis_label = "alert origin node"
p_fixed.toolbar.logo = None

p_random = figure(title="Random number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_random.circle(xs_random, ys, size=5, color="#000000", alpha=0.5)
p_random.xaxis.axis_label = "total time"
p_random.yaxis.axis_label = "alert origin node"
p_random.toolbar.logo = None

p_curr = figure(title="Centralized network", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_curr.circle(xs_curr, ys, size=5, color="#000000", alpha=0.5)
p_curr.xaxis.axis_label = "total time"
p_curr.yaxis.axis_label = "alert origin node"
p_curr.toolbar.logo = None

p = row(p_fixed, p_random, p_curr)
show(p)

In [ ]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.layouts import row
import secrets

NODES = 1000
NODE_CONNECTIONS = 100
NUMBER_LOOPS = 100
STEP = 1

current_connections = 5

xs = list()
ys = list()
xs_random = list()
ys_random = list()
xs_curr = list()
ys_curr = list()

while current_connections <= NODE_CONNECTIONS:
  G_alert = create_alert_graph(NODES, current_connections)
  G_alert_random = create_alert_graph(NODES, current_connections, True)

  random_generator = secrets.SystemRandom()
  alert_origin = random_generator.randrange(1, NODES - 1)

  time_stamp, nodes_alerted = alert_time_simulation(G_alert, alert_origin)
  time_stamp_random, nodes_alerted_random = alert_time_simulation(G_alert_random, alert_origin)

  xs.append(len(time_stamp))
  xs_random.append(len(time_stamp_random))
  ys.append(current_connections)

  current_connections += STEP

output_notebook()

p_fixed = figure(title="Fixed number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_fixed.circle(xs, ys, size=5, color="#000000", alpha=0.5)
p_fixed.xaxis.axis_label = "total time"
p_fixed.yaxis.axis_label = "connections per node"
p_fixed.toolbar.logo = None

p_random = figure(title="Random number of neighbors per node", plot_width=400, plot_height=400, tools=[BoxZoomTool(), ResetTool(), WheelZoomTool(), SaveTool()])
p_random.circle(xs_random, ys, size=5, color="#000000", alpha=0.5)
p_random.xaxis.axis_label = "total time"
p_random.yaxis.axis_label = "maximum connections per node"
p_random.toolbar.logo = None

p = row(p_fixed, p_random)
show(p)

### Alert Time Simulation